In [430]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [527]:
import numpy as np

class ActivationFunctions:
        
    def ReLu(data,derivative=False):
        if derivative:
            data=np.array(data)
            temp=np.sign(np.maximum(0,data))
        temp = np.array(data)
        return np.maximum(0,temp)
        
#     def Sign(data,derivative=False):
#         assert derivative==False
#         temp = np.array(data)
#         return np.sign(temp)
            
    def Sigmoid(data,derivative = False):
        if derivative:
            data=np.exp(-np.array(data))
            return data/((data+1)*(data+1))
        temp = np.array(data)
        return 1/(1+np.exp(-temp))
    def Default(data,derivative=False):
        return Sigmoid(data,derivative)
        if derivative:
            return 1
        return np.array(data)
        
#     def SoftMax(data,derivative=False):
#         assert derivative
#         temp = np.exp(np.array(data))
#         return temp/np.sum(temp)
    
class LossFunctions:
    
#     def MSE(estimator,goal):
# #         assert isinstance(estimator,np.array)
# #         assert isinstance(goal,np.array)
# #         print(estimator.shape, goal.shape)
# #         assert estimator.shape == goal.shape
# #         assert estimator.shape[0] == 1 or estimator.shape[1] ==1
#         estimator = np.array(estimator)
#         goal = np.array(goal)
        
#         return np.sum([i*i for i in (estimator-goal)])/len(np.max([estimator.shape[0] ,estimator.shape[1]]))
    
    def AE(estimator,goal,derivative=False):
        
        if derivative:
            return estimator-goal
        return (estimator-goal)*(estimator-goal)/2
        
        

class Layer:
    
    def __init__(self,shape,function=ActivationFunctions.Default) -> None:
        assert len(shape)==2
        assert isinstance(shape[0],int) and isinstance(shape[1],int)
        assert shape[0]>0 and shape[1]>0
        self.function=function
        self.shape = shape

        self._init_matrix()
        self.output=None
        self.input=None

    def __init__(self,shape_x:int,shape_y:int,function=ActivationFunctions.Default) -> None:
        assert shape_y>0 and shape_x>0

        self.shape = (shape_x,shape_y)
        self.function=function
        self._init_matrix()
        self.output=None
        self.input=None

    def _init_matrix(self):
#         self.matrix = np.random.randn(self.shape[0],self.shape[1])
        self.matrix = np.array([ [1 for i in range(self.shape[1])] for y in range(self.shape[0])])
#         self.bias=np.random.randn(1,self.shape[1])


    def forward(self,data,function=ActivationFunctions.Default):
        
        if function in [None,ActivationFunctions.Default]:
            function = self.function
        if function == None:
            self.output=np.dot(data,self.matrix)#-self.bias
            self.input=data
            return self.output
        else:
            #-self.bias
            self.dot = np.dot(data,self.matrix)
            self.output = function(self.dot)
            self.input=data
            return self.output
    

In [528]:
class Model:

    def __init__(self):
        self.layers=[]
        self.structure=[]
        self.learningFactor=0.1 # TODO implementation
        self.dataset={}
        self.loss_v=None
    def addLayer(self,numberOfNeurons:int,function=ActivationFunctions.Default):
        assert numberOfNeurons>0
        # TODO to validate function
        self.layers.append((numberOfNeurons,function))
        
    def compileModel(self):
        assert len(self.layers)>=2
        
        for i in range(len(self.layers)-1):
            self.structure.append(Layer(self.layers[i][0],self.layers[i+1][0],self.layers[i+1][1]))
            
    def forward(self,data):
        assert len(self.structure)>=2
        output = data
        for i in self.structure:
            output = i.forward(output)
        return output
    
    def upload_test_dataset(self,data): #TODO add validation
        self.dataset['test'] = data
        
    def upload_train_dataset(self,data): #TODO add validation
        self.dataset['train'] = data
    
    def loss(self,goal,function=LossFunctions.AE):
        return function(self.structure[-1].output,goal)
    
    def train(self):
        counter=10000
        while counter>=0:
            counter-=1
            
            for x,y in zip(self.dataset['train']['egzo'],self.dataset['train']['endo']):
                out = x
                for l in self.structure:
                    out = l.forward(out)
                self.loss_v=self.loss(y,LossFunctions.AE)
                print("LOSS_V: ",self.loss_v)
                
                dE_dz = [0]*len(self.structure)
                
                #dla ostatniej warstwy
                
                dE_dz[-1]= LossFunctions.AE(out,y,derivative=True) * self.structure[-1].function(self.structure[-1].output,derivative=True)
#                 print("####",dE_dz[-1])
                for l in range(-2,-(len(self.structure)+1),-1):
                    dE_dz[l] = np.sum(np.dot(self.structure[l+1].matrix,dE_dz[l+1]))*self.structure[l].function(self.structure[l].output,derivative=True)
#                     print("#$",dE_dz[l])
                    
               
                #output poprawnienie wag
                
                for l in range(-1,-(len(self.structure)+1),-1):
                    
#                         print(f"dE_dz[{l}]",dE_dz[l])
#                         print(f"self.structure[{l}].matrix.T",self.structure[l].matrix)
                        self.structure[l].matrix=self.structure[l].matrix-(self.learningFactor)*dE_dz[l]*self.structure[l].matrix
                
               
                
                
                
                
                
                
                
                
                
                
                
                
                '''
                correction=[0]*len(self.structure)
                #dla ostatniej warstwy:
                last_layer = self.structure[-1]


                #de/dz
                correction[-1]=(y-last_layer.output)*last_layer.function(last_layer.output,derivative=True)
                #print(correction[-1])

                for i in range(-2,-(len(self.structure)+1),-1):
                    #print("STRUCTURE ITERATION: ",i)

                    sum_of_corrections_from_next_layer =  np.sum(correction[i+1]*self.structure[i+1].matrix,axis=1)
                    #print("sum_of_corrections_from_next_layer",sum_of_corrections_from_next_layer)

                    correction[i]=sum_of_corrections_from_next_layer * self.structure[i].function(self.structure[i].output,derivative=True) 
                    #print(f"CORRECTION[{i}]= ",correction[i])

                print("CORRECTION",correction)

#                 print("\n\n\n\n\n")
                
                
                for l in range(-1,-(len(self.structure))-1,-1):
#                     print(l)
#                     print('$$$$',correction[l])
                    layer_reference=self.structure[l]
#                     print('layer_reference.matrix',layer_reference.matrix)
                    
                    for n_number,n in enumerate(layer_reference.matrix):

                        for w_number,w in enumerate(n):
#                             print("\tw ",w_number,w )
#                             print("\t\tcorrection   \n\t\tcorrection[l][n_number]",correction,"\n\t\t",correction[l][n_number])
#                             print("\t\layer_reference.input    \n\t\tlayer_reference.input[w_number]","\n\t\t",layer_reference.input,layer_reference.input[n_number])
#                             print("correction",correction)
#                             print("layer_reference.input",layer_reference.input)
#                             print("##",correction[l][w_number])
                            temp=correction[l][w_number]*layer_reference.input[n_number]
#                             print(temp)
                            layer_reference.matrix[n_number][w_number]-=0.05*temp
                
        
            
            
            ##obliczanie korekt
            
            # wartstwa ostatnia
                1. posiadam wartości błędu dla każdego z neuronów w warstwie ostatniej
                2. dla każdego z neuronów w warstwie ostatniej liczę różnicę między wyjśćiem a predykcją * derivative of activation function(output)
            # warstwy ukryte 
                3. liczę dla każdego z neuronów w warstwie ukrytej jaką ma sumę (wagę * korektę z poprzedniej warstwy w back propagation ze wszystkich neuronów)
                4. kolejno (suma (korekt * waga)) *(derivative_activation(function(output)))
            
            ## poprawianie wag:
            
            #outout layer:
                5. z podpunktu 2 biore wartości dla f'(output)*(y-y^), mnoże to * input do tego neuronu
                    odejmuje od wartości wagi tego neuronu learining*rate * wartość z 5 podpunktu
                    
            #HIDDEN
                iteracja po hidden:
                    iteracja po wagach w neuronnie h:
                6        error w stosunku do wagi = wartość z podpunktu 4 * to co na wejsciu do neuronu
                7. waga -= learning rate * error w stosunku do wagi
                        
            
            '''

In [529]:
model = Model()
model.addLayer(4,ActivationFunctions.Sigmoid)
model.addLayer(3,ActivationFunctions.Sigmoid)
model.addLayer(3,ActivationFunctions.Sigmoid)
model.addLayer(1,ActivationFunctions.Sigmoid)

model.compileModel()
train_dataset= {
    'egzo': np.array([[1,1,0,0],[1,0,0,0],[0,1,0,0],[0,0,0,0],[1,1,1,0],[1,0,1,0],[0,1,1,0],[0,0,1,0],[1,1,0,1],[1,0,0,1],[0,1,0,1],[0,0,0,1],[1,1,1,1],[1,0,1,1],[0,1,1,1],[0,0,1,1]]),
    'endo':np.array([[1],       [0],      [0],      [1],      [0],      [1],      [1],      [0],      [0],      [1],      [1],      [0],      [1],      [0],      [0],      [1]])
}
#print(train_dataset)
model.upload_train_dataset(train_dataset)
# for i in range(len(model.structure)):
#     print(model.structure[i].shape,end=f" {model.structure[i].function}\n ")
#model.forward(np.array([1,2,3,4,5]))
model.train()


LOSS_V:  [0.00164111]
LOSS_V:  [0.43915591]
LOSS_V:  [0.43565886]
LOSS_V:  [0.00379815]
LOSS_V:  [0.44047042]
LOSS_V:  [0.00226325]
LOSS_V:  [0.0022458]
LOSS_V:  [0.42931394]
LOSS_V:  [0.43444519]
LOSS_V:  [0.0027548]
LOSS_V:  [0.00273239]
LOSS_V:  [0.42246255]
LOSS_V:  [0.00269383]
LOSS_V:  [0.42849352]
LOSS_V:  [0.42502451]
LOSS_V:  [0.00362238]
LOSS_V:  [0.00359081]
LOSS_V:  [0.41193809]
LOSS_V:  [0.40801446]
LOSS_V:  [0.00709717]
LOSS_V:  [0.41544676]
LOSS_V:  [0.00463048]
LOSS_V:  [0.00458781]
LOSS_V:  [0.40144302]
LOSS_V:  [0.40886638]
LOSS_V:  [0.00539714]
LOSS_V:  [0.00534581]
LOSS_V:  [0.3943516]
LOSS_V:  [0.00512232]
LOSS_V:  [0.40265886]
LOSS_V:  [0.39887269]
LOSS_V:  [0.00667829]
LOSS_V:  [0.00661227]
LOSS_V:  [0.38375326]
LOSS_V:  [0.37973218]
LOSS_V:  [0.01145591]
LOSS_V:  [0.38908593]
LOSS_V:  [0.00807271]
LOSS_V:  [0.00799053]
LOSS_V:  [0.37354938]
LOSS_V:  [0.38251022]
LOSS_V:  [0.00908826]
LOSS_V:  [0.0089943]
LOSS_V:  [0.36678681]
LOSS_V:  [0.00848969]
LOSS_V:  [0.37

LOSS_V:  [0.17108971]
LOSS_V:  [0.17402923]
LOSS_V:  [0.08565535]
LOSS_V:  [0.08531197]
LOSS_V:  [0.17067596]
LOSS_V:  [0.08359601]
LOSS_V:  [0.17408732]
LOSS_V:  [0.1733593]
LOSS_V:  [0.08610582]
LOSS_V:  [0.08576485]
LOSS_V:  [0.17005893]
LOSS_V:  [0.16940038]
LOSS_V:  [0.08950949]
LOSS_V:  [0.17273148]
LOSS_V:  [0.08652984]
LOSS_V:  [0.08619118]
LOSS_V:  [0.16948049]
LOSS_V:  [0.17231216]
LOSS_V:  [0.08681405]
LOSS_V:  [0.08647696]
LOSS_V:  [0.16909411]
LOSS_V:  [0.08479705]
LOSS_V:  [0.17238505]
LOSS_V:  [0.17168647]
LOSS_V:  [0.08723963]
LOSS_V:  [0.08690492]
LOSS_V:  [0.16851749]
LOSS_V:  [0.1678851]
LOSS_V:  [0.09054043]
LOSS_V:  [0.17109963]
LOSS_V:  [0.08764045]
LOSS_V:  [0.087308]
LOSS_V:  [0.16797648]
LOSS_V:  [0.17070743]
LOSS_V:  [0.08790922]
LOSS_V:  [0.0875783]
LOSS_V:  [0.16761488]
LOSS_V:  [0.08593347]
LOSS_V:  [0.17079308]
LOSS_V:  [0.17012183]
LOSS_V:  [0.08831186]
LOSS_V:  [0.08798327]
LOSS_V:  [0.16707488]
LOSS_V:  [0.16646679]
LOSS_V:  [0.09151532]
LOSS_V:  [0.169

LOSS_V:  [0.10511181]
LOSS_V:  [0.14596849]
LOSS_V:  [0.10414034]
LOSS_V:  [0.14750027]
LOSS_V:  [0.14720108]
LOSS_V:  [0.10543459]
LOSS_V:  [0.10523219]
LOSS_V:  [0.14583109]
LOSS_V:  [0.14555646]
LOSS_V:  [0.10709717]
LOSS_V:  [0.14706086]
LOSS_V:  [0.1055482]
LOSS_V:  [0.10534681]
LOSS_V:  [0.14570038]
LOSS_V:  [0.1469663]
LOSS_V:  [0.10562488]
LOSS_V:  [0.10542417]
LOSS_V:  [0.14561224]
LOSS_V:  [0.10446645]
LOSS_V:  [0.14711723]
LOSS_V:  [0.14682367]
LOSS_V:  [0.10574063]
LOSS_V:  [0.10554095]
LOSS_V:  [0.14547929]
LOSS_V:  [0.14520977]
LOSS_V:  [0.10737617]
LOSS_V:  [0.14668799]
LOSS_V:  [0.10585086]
LOSS_V:  [0.10565216]
LOSS_V:  [0.14535279]
LOSS_V:  [0.14659648]
LOSS_V:  [0.10592526]
LOSS_V:  [0.10572723]
LOSS_V:  [0.14526748]
LOSS_V:  [0.1047829]
LOSS_V:  [0.14674656]
LOSS_V:  [0.14645844]
LOSS_V:  [0.1060376]
LOSS_V:  [0.10584056]
LOSS_V:  [0.14513878]
LOSS_V:  [0.14487418]
LOSS_V:  [0.10764693]
LOSS_V:  [0.14632709]
LOSS_V:  [0.10614459]
LOSS_V:  [0.10594852]
LOSS_V:  [0.14

LOSS_V:  [0.13999367]
LOSS_V:  [0.11142873]
LOSS_V:  [0.11128222]
LOSS_V:  [0.13909987]
LOSS_V:  [0.13994855]
LOSS_V:  [0.11146728]
LOSS_V:  [0.11132114]
LOSS_V:  [0.13905764]
LOSS_V:  [0.1106329]
LOSS_V:  [0.14007342]
LOSS_V:  [0.13988031]
LOSS_V:  [0.1115256]
LOSS_V:  [0.11138004]
LOSS_V:  [0.13899377]
LOSS_V:  [0.13881558]
LOSS_V:  [0.11265537]
LOSS_V:  [0.13981506]
LOSS_V:  [0.11158139]
LOSS_V:  [0.11143638]
LOSS_V:  [0.1389327]
LOSS_V:  [0.13977096]
LOSS_V:  [0.11161912]
LOSS_V:  [0.11147448]
LOSS_V:  [0.13889142]
LOSS_V:  [0.11079348]
LOSS_V:  [0.1398949]
LOSS_V:  [0.13970425]
LOSS_V:  [0.11167621]
LOSS_V:  [0.11153213]
LOSS_V:  [0.13882898]
LOSS_V:  [0.13865304]
LOSS_V:  [0.11279295]
LOSS_V:  [0.13964046]
LOSS_V:  [0.11173082]
LOSS_V:  [0.11158728]
LOSS_V:  [0.13876927]
LOSS_V:  [0.13959734]
LOSS_V:  [0.11176776]
LOSS_V:  [0.11162458]
LOSS_V:  [0.1387289]
LOSS_V:  [0.11095068]
LOSS_V:  [0.13972036]
LOSS_V:  [0.13953212]
LOSS_V:  [0.11182365]
LOSS_V:  [0.11168102]
LOSS_V:  [0.138

LOSS_V:  [0.11490082]
LOSS_V:  [0.13523044]
LOSS_V:  [0.13583985]
LOSS_V:  [0.11503289]
LOSS_V:  [0.11492268]
LOSS_V:  [0.13520742]
LOSS_V:  [0.11440766]
LOSS_V:  [0.13593977]
LOSS_V:  [0.13580269]
LOSS_V:  [0.11506566]
LOSS_V:  [0.11495578]
LOSS_V:  [0.13517254]
LOSS_V:  [0.13504566]
LOSS_V:  [0.11589149]
LOSS_V:  [0.13576703]
LOSS_V:  [0.1150971]
LOSS_V:  [0.11498755]
LOSS_V:  [0.13513908]
LOSS_V:  [0.1357429]
LOSS_V:  [0.11511838]
LOSS_V:  [0.11500905]
LOSS_V:  [0.13511644]
LOSS_V:  [0.11449826]
LOSS_V:  [0.13584214]
LOSS_V:  [0.13570636]
LOSS_V:  [0.11515062]
LOSS_V:  [0.11504162]
LOSS_V:  [0.13508215]
LOSS_V:  [0.13495646]
LOSS_V:  [0.11596922]
LOSS_V:  [0.13567129]
LOSS_V:  [0.11518156]
LOSS_V:  [0.11507289]
LOSS_V:  [0.13504924]
LOSS_V:  [0.13564756]
LOSS_V:  [0.11520251]
LOSS_V:  [0.11509405]
LOSS_V:  [0.13502698]
LOSS_V:  [0.11458743]
LOSS_V:  [0.13574613]
LOSS_V:  [0.13561162]
LOSS_V:  [0.11523424]
LOSS_V:  [0.1151261]
LOSS_V:  [0.13499325]
LOSS_V:  [0.13486873]
LOSS_V:  [0.1

...

LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [

LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [

LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [

LOSS_V:  [0.12500002]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500003]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [

LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499997]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12499998]
LOSS_V:  [0.12500002]
LOSS_V:  [0.12499998]
LOSS_V:  [

In [533]:
model.forward(np.array([1,1,0,0]))

array([0.50000005])

In [343]:
(np.array([[1,1],[1,1],[1,1]]).T*np.array([2,2,2])).T

array([[2, 2],
       [2, 2],
       [2, 2]])

In [531]:
DEBUG=False

In [42]:
ActivationFunctions.SoftMax(np.linspace(-1,1,100))

1.0000000000000002

In [111]:
a=np.array([[1,2],[7,8]])
np.sum(a,axis=1)

array([ 8, 10])


Taka jest docelowa funckja LOSS czyli taka którą minimalizujemy.

```1```- indidator function https://www.wikiwand.com/en/Indicator_function

```i``` iteruje sie po obserwacjach

```c``` iteruje sie po klasach

$p_{model} [y_i \in C_c ]$ prawdopodobieństwo, że obserwacja i należy do klasy c

$-1/N*\Sigma_{i=1} ^N \Sigma_{c=1} ^C 1_{y_{i} \in C_{c}} log(p_{model}[y_i \in C_{c}]) $